<small><i>This notebook was put together by [Jake Vanderplas](http://www.vanderplas.com) for PyCon 2014. Source and license info is on [GitHub](https://github.com/jakevdp/sklearn_pycon2014/).</i></small>

# Scipy Sparse Matrices

**Sparse Matrices** are very nice in some situations.  

For example, in some machine learning tasks, especially those associated
with textual analysis, the data may be mostly zeros.  

Storing all these zeros is very inefficient.  

We can create and manipulate sparse matrices as follows:

In [2]:
import numpy as np

In [4]:
# Create a random array with a lot of zeros
X = np.random.random((10, 5))
print(X)

[[ 0.92071168  0.66941621  0.30097014  0.8668366   0.94764952]
 [ 0.16978456  0.59292571  0.78884569  0.76910071  0.56415941]
 [ 0.096867    0.96869327  0.8643055   0.0297782   0.11921581]
 [ 0.22387061  0.71015351  0.45882072  0.34433871  0.85566776]
 [ 0.22217957  0.83387745  0.40605966  0.41212024  0.65548993]
 [ 0.53416368  0.92406734  0.66444729  0.57218427  0.48198361]
 [ 0.37469397  0.33167227  0.9107519   0.03360275  0.20205017]
 [ 0.39939621  0.61025928  0.14715445  0.86871212  0.25921407]
 [ 0.07210422  0.99690991  0.31477122  0.49698491  0.34563232]
 [ 0.10310154  0.3806856   0.77690381  0.46116052  0.43330533]]


In [5]:
X[X < 0.7] = 0
print(X)

[[ 0.92071168  0.          0.          0.8668366   0.94764952]
 [ 0.          0.          0.78884569  0.76910071  0.        ]
 [ 0.          0.96869327  0.8643055   0.          0.        ]
 [ 0.          0.71015351  0.          0.          0.85566776]
 [ 0.          0.83387745  0.          0.          0.        ]
 [ 0.          0.92406734  0.          0.          0.        ]
 [ 0.          0.          0.9107519   0.          0.        ]
 [ 0.          0.          0.          0.86871212  0.        ]
 [ 0.          0.99690991  0.          0.          0.        ]
 [ 0.          0.          0.77690381  0.          0.        ]]


In [6]:
from scipy import sparse

# turn X into a csr (Compressed-Sparse-Row) matrix
X_csr = sparse.csr_matrix(X)
print(X_csr)

  (0, 0)	0.920711681384
  (0, 3)	0.866836604396
  (0, 4)	0.947649515452
  (1, 2)	0.788845688727
  (1, 3)	0.769100712548
  (2, 1)	0.968693269052
  (2, 2)	0.864305496772
  (3, 1)	0.710153508323
  (3, 4)	0.855667757095
  (4, 1)	0.833877448584
  (5, 1)	0.924067342994
  (6, 2)	0.910751902907
  (7, 3)	0.868712121221
  (8, 1)	0.996909907387
  (9, 2)	0.776903807028


In [7]:
# convert the sparse matrix to a dense array
print(X_csr.toarray())

[[ 0.92071168  0.          0.          0.8668366   0.94764952]
 [ 0.          0.          0.78884569  0.76910071  0.        ]
 [ 0.          0.96869327  0.8643055   0.          0.        ]
 [ 0.          0.71015351  0.          0.          0.85566776]
 [ 0.          0.83387745  0.          0.          0.        ]
 [ 0.          0.92406734  0.          0.          0.        ]
 [ 0.          0.          0.9107519   0.          0.        ]
 [ 0.          0.          0.          0.86871212  0.        ]
 [ 0.          0.99690991  0.          0.          0.        ]
 [ 0.          0.          0.77690381  0.          0.        ]]


In [8]:
# Sparse matrices support linear algebra:
y = np.random.random(X_csr.shape[1])
z1 = X_csr.dot(y)
z2 = X.dot(y)
np.allclose(z1, z2)

True

* The CSR representation can be very efficient for computations, but it is not as good for adding elements.  

* For that, the **LIL** (List-In-List) representation is better:

In [9]:
# Create an empty LIL matrix and add some items
X_lil = sparse.lil_matrix((5, 5))

for i, j in np.random.randint(0, 5, (15, 2)):
    X_lil[i, j] = i + j

print(X_lil)
print(X_lil.toarray())

  (0, 2)	2.0
  (1, 1)	2.0
  (1, 2)	3.0
  (1, 3)	4.0
  (2, 0)	2.0
  (2, 3)	5.0
  (2, 4)	6.0
  (3, 0)	3.0
  (3, 1)	4.0
  (3, 4)	7.0
  (4, 2)	6.0
  (4, 3)	7.0
[[ 0.  0.  2.  0.  0.]
 [ 0.  2.  3.  4.  0.]
 [ 2.  0.  0.  5.  6.]
 [ 3.  4.  0.  0.  7.]
 [ 0.  0.  6.  7.  0.]]


* Often, once an LIL matrix is created, it is useful to convert it to a CSR format 
    * **Note**: many scikit-learn algorithms require CSR or CSC format

In [10]:
X_csr = X_lil.tocsr()
print(X_csr)

  (0, 2)	2.0
  (1, 1)	2.0
  (1, 2)	3.0
  (1, 3)	4.0
  (2, 0)	2.0
  (2, 3)	5.0
  (2, 4)	6.0
  (3, 0)	3.0
  (3, 1)	4.0
  (3, 4)	7.0
  (4, 2)	6.0
  (4, 3)	7.0


There are several other sparse formats that can be useful for various problems:

- `CSC` (compressed sparse column)
- `BSR` (block sparse row)
- `COO` (coordinate)
- `DIA` (diagonal)
- `DOK` (dictionary of keys)

## CSC - Compressed Sparse Column

**Advantages of the CSC format**

    * efficient arithmetic operations CSC + CSC, CSC * CSC, etc.
    * efficient column slicing
    * fast matrix vector products (CSR, BSR may be faster)

**Disadvantages of the CSC format**

    * slow row slicing operations (consider CSR)
    * changes to the sparsity structure are expensive (consider LIL or DOK)

### BSR - Block Sparse Row

The Block Compressed Row (`BSR`) format is very similar to the Compressed Sparse Row (`CSR`) format. 

BSR is appropriate for sparse matrices with *dense sub matrices* like the example below. 

Block matrices often arise in *vector-valued* finite element discretizations. 

In such cases, BSR is **considerably more efficient** than CSR and CSC for many sparse arithmetic operations.

In [12]:
from scipy.sparse import bsr_matrix

indptr = np.array([0, 2, 3, 6])
indices = np.array([0, 2, 2, 0, 1, 2])
data = np.array([1, 2, 3, 4, 5, 6]).repeat(4).reshape(6, 2, 2)
bsr_matrix((data,indices,indptr), shape=(6, 6)).toarray()

array([[1, 1, 0, 0, 2, 2],
       [1, 1, 0, 0, 2, 2],
       [0, 0, 0, 0, 3, 3],
       [0, 0, 0, 0, 3, 3],
       [4, 4, 5, 5, 6, 6],
       [4, 4, 5, 5, 6, 6]])

## COO - Coordinate Sparse Matrix

**Advantages of the CSC format**

    * facilitates fast conversion among sparse formats
    * permits duplicate entries (see example)
    * very fast conversion to and from CSR/CSC formats

**Disadvantages of the CSC format**

    * does not directly support arithmetic operations and slicing
    
** Intended Usage**

    * COO is a fast format for constructing sparse matrices
    * Once a matrix has been constructed, convert to CSR or CSC format for fast arithmetic and matrix vector
    operations
    * By default when converting to CSR or CSC format, duplicate (i,j) entries will be summed together. 
    This facilitates efficient construction of finite element matrices and the like.


## DOK - Dictionary of Keys

Sparse matrices can be used in arithmetic operations: they support addition, subtraction, multiplication, division, and matrix power.

Allows for efficient O(1) access of individual elements. Duplicates are not allowed. Can be efficiently converted to a coo_matrix once constructed.

In [15]:
from scipy.sparse import dok_matrix
S = dok_matrix((5, 5), dtype=np.float32)
for i in range(5):
    for j in range(i, 5):
        S[i,j] = i+j
        
S.toarray()

array([[ 0.,  1.,  2.,  3.,  4.],
       [ 0.,  2.,  3.,  4.,  5.],
       [ 0.,  0.,  4.,  5.,  6.],
       [ 0.,  0.,  0.,  6.,  7.],
       [ 0.,  0.,  0.,  0.,  8.]], dtype=float32)

The ``scipy.sparse`` submodule also has a lot of functions for sparse matrices
including linear algebra, sparse solvers, graph algorithms, and much more.